In [0]:
silver_path = "/mnt/silver/delta/airline_delays"           # silver delta path
gold_base_path = "/mnt/gold-parquet/airline_delays_gold"            # base path for gold Delta tables
gold_monthly_path = f"{gold_base_path}/monthly"             # partitioned by year/month
gold_carrier_path = f"{gold_base_path}/carrier"             # partitioned by carrier/year/month
gold_causes_path = f"{gold_base_path}/causes" 
gold_master_path = f"{gold_base_path}/master"

In [0]:

storage_account_name = "saflightdelays"
container_name = "gold"
container_name_parq='gold-parquet'
storage_account_key = ""

mount_point = f"/mnt/{container_name_parq}"
source_url = f"wasbs://{container_name_parq}@{storage_account_name}.blob.core.windows.net"

# Check if already mounted and unmount if needed
for mnt in dbutils.fs.mounts():
    if mnt.mountPoint == mount_point:
        print(f"Already mounted at {mount_point}, unmounting first...")
        dbutils.fs.unmount(mount_point)

# Mount
dbutils.fs.mount(
    source=source_url,
    mount_point=mount_point,
    extra_configs={f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_key}
)

print(f"Mounted successfully: {mount_point}")

Already mounted at /mnt/gold-parquet, unmounting first...
/mnt/gold-parquet has been unmounted.
Mounted successfully: /mnt/gold-parquet


In [0]:

from pyspark.sql import functions as F
from pyspark.sql.types import DoubleType, IntegerType
from delta.tables import DeltaTable

# Paths 
silver_path = "/mnt/silver/delta/airline_delays"           # silver delta path
gold_base_path = "/mnt/gold/airline_delays_gold"            # base path for gold Delta tables
gold_monthly_path = f"{gold_base_path}/monthly"             # partitioned by year/month
gold_carrier_path = f"{gold_base_path}/carrier"             # partitioned by carrier/year/month
gold_airport_path = f"{gold_base_path}/airport"             # partitioned by airport/year/month

#1) Read silver table 
df = spark.read.format("delta").load(silver_path)

df = df.na.fill({c: 0 for c in ["arr_flights", "arr_del15", "carrier_ct", "weather_ct", "nas_ct", "security_ct", "late_aircraft_ct", "arr_cancelled", "arr_diverted", "arr_delay", "carrier_delay"]})


df = (df
      .withColumn("year", F.col("year").cast(IntegerType()))
      .withColumn("month", F.col("month").cast(IntegerType()))
      .withColumn("arr_flights", F.col("arr_flights").cast(DoubleType()))
      .withColumn("arr_del15", F.col("arr_del15").cast(DoubleType()))
      .withColumn("carrier_ct", F.col("carrier_ct").cast(DoubleType()))
      .withColumn("weather_ct", F.col("weather_ct").cast(DoubleType()))
      .withColumn("nas_ct", F.col("nas_ct").cast(DoubleType()))
      .withColumn("security_ct", F.col("security_ct").cast(DoubleType()))
      .withColumn("late_aircraft_ct", F.col("late_aircraft_ct").cast(DoubleType()))
      .withColumn("arr_cancelled", F.col("arr_cancelled").cast(DoubleType()))
      .withColumn("arr_diverted", F.col("arr_diverted").cast(DoubleType()))
      .withColumn("arr_delay", F.col("arr_delay").cast(DoubleType()))
      .withColumn("carrier_delay", F.col("carrier_delay").cast(DoubleType()))
     )

In [0]:
# Create a canonical timestamp column if available; otherwise derive a synthetic date from year/month

df = df.withColumn("year_month", F.concat_ws("-", F.col("year"), F.lpad(F.col("month").cast("string"), 2, "0")))

# 2) Define KPI formulas 
# delay_rate = arr_del15 / arr_flights  (fraction of flights delayed >15)
# avg_delay_per_flight = arr_delay / arr_flights (minutes per flight)
# cancel_rate = arr_cancelled / arr_flights
# divert_rate = arr_diverted / arr_flights
# percent_by_cause = cause_ct / sum_of_cause_cts  (normalize carrier/weather/nas/security/late_aircraft)
# also compute P95 and median if you have per-flight delay distribution (we have aggregated sums so P95 needs original events)

cause_cols = ["carrier_ct", "weather_ct", "nas_ct", "security_ct", "late_aircraft_ct"]

# Add basic KPIs at row level (guard divide-by-zero)
df_k = (df
       .withColumn("delay_rate", F.when(F.col("arr_flights") > 0, F.col("arr_del15") / F.col("arr_flights")).otherwise(F.lit(0.0)))
       .withColumn("avg_delay_per_flight", F.when(F.col("arr_flights") > 0, F.col("arr_delay") / F.col("arr_flights")).otherwise(F.lit(0.0)))
       .withColumn("cancel_rate", F.when(F.col("arr_flights") > 0, F.col("arr_cancelled") / F.col("arr_flights")).otherwise(F.lit(0.0)))
       .withColumn("divert_rate", F.when(F.col("arr_flights") > 0, F.col("arr_diverted") / F.col("arr_flights")).otherwise(F.lit(0.0)))
      )

# compute sum of cause counts (for normalization)
df_k = df_k.withColumn("cause_total", sum([F.col(c) for c in cause_cols]))

for c in cause_cols:
    df_k = df_k.withColumn(f"{c}_pct", F.when(F.col("cause_total") > 0, F.col(c) / F.col("cause_total")).otherwise(F.lit(0.0)))


In [0]:
display(df_k)

year month carrier carrier_name airport airport_name arr_flights arr_del15 carrier_ct weather_ct nas_ct security_ct late_aircraft_ct arr_cancelled arr_diverted arr_delay carrier_delay year_month delay_rate avg_delay_per_flight cancel_rate divert_rate cause_total carrier_ct_pct weather_ct_pct nas_ct_pct security_ct_pct late_aircraft_ct_pct 2025 7 YV Mesa Airlines Inc. CRP Corpus Christi, TX: Corpus Christi International 19.0 4.0 0.71 0.3 0.7 0.0 2.29 1.0 0.0 823.0 45.0 2025-07 0.21052631578947367 43.31578947368421 0.05263157894736842 0.0 4.0 0.1775 0.075 0.175 0.0 0.5725 2025 7 YV Mesa Airlines Inc. CVG Cincinnati, OH: Cincinnati/Northern Kentucky International 75.0 14.0 7.64 1.0 3.57 0.0 1.79 0.0 0.0 722.0 485.0 2025-07 0.18666666666666668 9.626666666666667 0.0 0.0 14.0 0.5457142857142857 0.07142857142857142 0.255 0.0 0.12785714285714286 2025 7 YV Mesa Airlines Inc. DFW Dallas/Fort Worth, TX: Dallas/Fort Worth International 97.0 23.0 8.09 0.73 4.85 0.0 9.33 1.0 0.0 2125.0 655.0 2025-07 0.23711340206185566 21.90721649484536 0.010309278350515464 0.0 23.0 0.3517391304347826 0.03173913043478261 0.21086956521739128 0.0 0.4056521739130435 2025 7 YV Mesa Airlines Inc. GUC Gunnison, CO: Gunnison-Crested Butte Regional 8.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 150.0 0.0 2025-07 0.125 18.75 0.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 2025 7 YV Mesa Airlines Inc. IAD Washington, DC: Washington Dulles International 978.0 234.0 52.94 14.27 67.41 0.0 99.39 48.0 6.0 23417.0 3756.0 2025-07 0.2392638036809816 23.943762781186095 0.049079754601226995 0.006134969325153374 234.01 0.22622964830562797 0.060980299987180034 0.28806461262339217 0.0 0.42472543908379984 2025 5 OO SkyWest Airlines Inc. BFL Bakersfield, CA: Meadows Field 133.0 30.0 12.31 3.0 8.98 0.0 5.71 0.0 0.0 2589.0 563.0 2025-05 0.22556390977443608 19.466165413533833 0.0 0.0 30.0 0.4103333333333333 0.1 0.29933333333333334 0.0 0.19033333333333333 2025 5 OO SkyWest Airlines Inc. BGM Binghamton, NY: Greater Binghamton/Edwin A. Link Field 25.0 2.0 2.0 0.0 0.0 0.0 0.0 0.0 1.0 60.0 60.0 2025-05 0.08 2.4 0.0 0.04 2.0 1.0 0.0 0.0 0.0 0.0 2025 5 OO SkyWest Airlines Inc. BHM Birmingham, AL: Birmingham-Shuttlesworth International 176.0 54.0 31.88 6.83 7.12 0.0 8.18 1.0 0.0 3970.0 2103.0 2025-05 0.3068181818181818 22.556818181818183 0.005681818181818182 0.0 54.01 0.5902610627661544 0.1264580633216071 0.13182743936308092 0.0 0.15145343454915755 2025 5 OO SkyWest Airlines Inc. BIL Billings, MT: Billings Logan International 175.0 24.0 10.29 1.68 4.63 0.0 7.4 1.0 1.0 1579.0 470.0 2025-05 0.13714285714285715 9.022857142857143 0.005714285714285714 0.005714285714285714 24.0 0.42874999999999996 0.06999999999999999 0.19291666666666665 0.0 0.30833333333333335 2025 5 OO SkyWest Airlines Inc. BIS Bismarck/Mandan, ND: Bismarck Municipal 144.0 29.0 8.59 4.71 7.3 0.0 8.4 2.0 1.0 4274.0 1089.0 2025-05 0.2013888888888889 29.680555555555557 0.013888888888888888 0.006944444444444444 29.0 0.2962068965517241 0.16241379310344828 0.2517241379310345 0.0 0.2896551724137931 2025 5 OO SkyWest Airlines Inc. BJI Bemidji, MN: Bemidji Regional 62.0 9.0 6.55 2.0 0.45 0.0 0.0 0.0 0.0 1329.0 1194.0 2025-05 0.14516129032258066 21.43548387096774 0.0 0.0 9.0 0.7277777777777777 0.2222222222222222 0.05 0.0 0.0 2025 5 OO SkyWest Airlines Inc. BLI Bellingham, WA: Bellingham International 119.0 25.0 5.0 0.0 5.96 0.0 14.04 0.0 0.0 916.0 168.0 2025-05 0.21008403361344538 7.697478991596639 0.0 0.0 25.0 0.2 0.0 0.2384 0.0 0.5616 2025 5 OO SkyWest Airlines Inc. BNA Nashville, TN: Nashville International 311.0 85.0 51.66 16.24 11.82 0.0 5.28 6.0 1.0 5055.0 3107.0 2025-05 0.2733118971061093 16.2540192926045 0.01929260450160772 0.003215434083601286 85.0 0.6077647058823529 0.19105882352941175 0.13905882352941176 0.0 0.062117647058823534 2025 5 OO SkyWest Airlines Inc. BOI Boise, ID: Boise Air Terminal 909.0 116.0 43.76 13.3 26.18 0.13 32.62 1.0 0.0 6286.0 2128.0 2025-05 0.1276127612761276 6.915291529152915 0.0011001100110011 0.0 115.99000000000001 0.37727390292266

In [0]:
# 3) Monthly-level aggregations (gold_monthly) 
agg_monthly = (df_k
               .groupBy("year", "month", "year_month")
               .agg(
                   F.sum("arr_flights").alias("total_arr_flights"),
                   F.sum("arr_del15").alias("total_arr_del15"),
                   F.sum("arr_delay").alias("total_arr_delay_minutes"),
                   F.sum("arr_cancelled").alias("total_arr_cancelled"),
                   F.sum("arr_diverted").alias("total_arr_diverted"),
                   *[F.sum(c).alias(f"sum_{c}") for c in cause_cols]
               )
              )

agg_monthly = (agg_monthly
               .withColumn("delay_rate", F.when(F.col("total_arr_flights")>0, F.col("total_arr_del15")/F.col("total_arr_flights")).otherwise(0.0))
               .withColumn("avg_delay_per_flight", F.when(F.col("total_arr_flights")>0, F.col("total_arr_delay_minutes")/F.col("total_arr_flights")).otherwise(0.0))
               .withColumn("cancel_rate", F.when(F.col("total_arr_flights")>0, F.col("total_arr_cancelled")/F.col("total_arr_flights")).otherwise(0.0))
               .withColumn("divert_rate", F.when(F.col("total_arr_flights")>0, F.col("total_arr_diverted")/F.col("total_arr_flights")).otherwise(0.0))
              )

# Add normalized cause shares
for c in cause_cols:
    agg_monthly = agg_monthly.withColumn(f"{c}_pct", F.when((F.col("sum_" + c) + 0) > 0, F.col("sum_" + c) / (F.expr(" + ".join([f"sum_{col}" for col in cause_cols])))).otherwise(0.0))


In [0]:
display(agg_monthly.limit(5))

year month year_month total_arr_flights total_arr_del15 total_arr_delay_minutes total_arr_cancelled total_arr_diverted sum_carrier_ct sum_weather_ct sum_nas_ct sum_security_ct sum_late_aircraft_ct delay_rate avg_delay_per_flight cancel_rate divert_rate carrier_ct_pct weather_ct_pct nas_ct_pct security_ct_pct late_aircraft_ct_pct 2024 12 2024-12 631944.0 132515.0 9585044.0 4579.0 1752.0 43489.29000000008 5391.969999999997 34704.26999999997 308.71999999999974 48620.75999999997 0.20969421341131492 15.16755282113605 0.007245895205904321 0.0027723975542136643 0.3281838789432237 0.040689503777722964 0.2618893512516051 0.0023296983488889276 0.36690756767855937 2024 8 2024-08 660639.0 150010.0 1.129244E7 13434.0 2174.0 46480.130000000005 6147.579999999993 41086.280000000086 331.8900000000001 55964.15999999992 0.22706803564427774 17.093208242322962 0.020334857615127173 0.0032907533463813064 0.30984679425457123 0.040981123663456076 0.273890200949217 0.002212451913218609 0.37306942921953706 2025 5 2025-05 667586.0 155262.0 1.1438449E7 7549.0 1898.0 43212.07000000002 7216.090000000004 49775.120000000024 203.42 54855.019999999975 0.23257228282198847 17.134045651047206 0.011307906397078429 0.002843079393516341 0.27831760462269783 0.04647694228815707 0.32058848761948544 0.0013101748454158561 0.3533067906242438 2025 4 2025-04 644084.0 124749.0 8747498.0 5291.0 1443.0 37564.129999999925 4662.500000000001 36994.31999999997 231.10999999999993 45297.05999999998 0.19368436415125978 13.5812999546643 0.0082147670179666 0.002240391004899982 0.3011173946557696 0.03737501314638537 0.2965497472046296 0.0018525982387691405 0.3631052467544463 2024 6 2024-06 651799.0 157404.0 1.1642182E7 8315.0 2105.0 50697.429999999935 6373.670000000002 38325.49000000005 435.89000000000016 61571.86999999999 0.2414916254857709 17.86161377970816 0.012757000240871803 0.0032295232119104204 0.3220840465971871 0.040492337092335774 0.24348431285412414 0.002769237317774256 0.39117006613857874

In [0]:
#4) Carrier-level KPIs (gold_carrier) 
agg_carrier = (df_k
               .groupBy("carrier", "carrier_name", "year", "month")
               .agg(
                   F.sum("arr_flights").alias("total_arr_flights"),
                   F.sum("arr_del15").alias("total_arr_del15"),
                   F.sum("arr_delay").alias("total_arr_delay_minutes"),
                   F.sum("arr_cancelled").alias("total_arr_cancelled"),
                   F.sum("arr_diverted").alias("total_arr_diverted"),
                   *[F.sum(c).alias(f"sum_{c}") for c in cause_cols]
               )
              )

agg_carrier = (agg_carrier
               .withColumn("delay_rate", F.when(F.col("total_arr_flights")>0, F.col("total_arr_del15")/F.col("total_arr_flights")).otherwise(0.0))
               .withColumn("avg_delay_per_flight", F.when(F.col("total_arr_flights")>0, F.col("total_arr_delay_minutes")/F.col("total_arr_flights")).otherwise(0.0))
               .withColumn("cancel_rate", F.when(F.col("total_arr_flights")>0, F.col("total_arr_cancelled")/F.col("total_arr_flights")).otherwise(0.0))
               .withColumn("divert_rate", F.when(F.col("total_arr_flights")>0, F.col("total_arr_diverted")/F.col("total_arr_flights")).otherwise(0.0))
              )

for c in cause_cols:
    agg_carrier = agg_carrier.withColumn(f"{c}_pct", F.when((F.col("sum_" + c) + 0) > 0, F.col("sum_" + c) / (F.expr(" + ".join([f"sum_{col}" for col in cause_cols])))).otherwise(0.0))


In [0]:
agg_carrier.limit(5).display()

carrier carrier_name year month total_arr_flights total_arr_del15 total_arr_delay_minutes total_arr_cancelled total_arr_diverted sum_carrier_ct sum_weather_ct sum_nas_ct sum_security_ct sum_late_aircraft_ct delay_rate avg_delay_per_flight cancel_rate divert_rate carrier_ct_pct weather_ct_pct nas_ct_pct security_ct_pct late_aircraft_ct_pct 9E Endeavor Air Inc. 2025 2 16896.0 3312.0 243201.0 339.0 41.0 681.68 121.50000000000001 1241.4599999999996 1.44 1265.9599999999998 0.19602272727272727 14.393998579545455 0.020063920454545456 0.0024266098484848485 0.20581877030470652 0.03668433956111643 0.37483242956002943 4.347773577613798E-4 0.38222968321638634 OH PSA Airlines Inc. 2024 5 18829.0 5329.0 429500.0 178.0 64.0 1206.2900000000002 333.8700000000002 1532.06 17.5 2239.230000000001 0.28302087205905785 22.810558181528492 0.009453502575813904 0.0033990121620903926 0.2263654190788054 0.06265211720883103 0.28749753703825326 0.0032839489955807425 0.42020097767852965 G7 GoJet Airlines LLC d/b/a United Express 2025 2 5220.0 1394.0 140921.0 150.0 6.0 289.44 25.21 461.64999999999986 0.0 617.72 0.2670498084291188 26.996360153256706 0.028735632183908046 0.0011494252873563218 0.207629732715456 0.01808438903315591 0.3311645457023571 0.0 0.4431213325490309 G7 GoJet Airlines LLC d/b/a United Express 2024 11 5558.0 1435.0 137827.0 40.0 14.0 303.82 8.28 503.42 0.16 619.2900000000001 0.25818639798488663 24.797948902482908 0.007196833393306945 0.0025188916876574307 0.21172568067625105 0.005770155473633595 0.350822665282201 1.1150058886248492E-4 0.4315699979790519 QX Horizon Air 2025 1 7754.0 1285.0 66695.0 143.0 32.0 324.39000000000004 59.44 372.63 2.64 525.95 0.1657209182357493 8.601367036368327 0.018442094402888833 0.0041269022440030955 0.2524337574413447 0.046255009532703 0.28997315279561103 0.002054394770631493 0.4092836854597097

In [0]:
# 5) Delay Causes KPI 
from pyspark.sql.functions import round as round_, sum as sum_, col, expr

causes = ["carrier_ct", "weather_ct", "nas_ct", "security_ct", "late_aircraft_ct"]

agg_causes = (
    df_k
    .groupBy("carrier", "carrier_name", "year", "month")
    .agg(*[sum_(col(c).cast("double")).alias(f"sum_{c}") for c in causes])
)

# compute total and percent shares
total_expr = " + ".join([f"sum_{c}" for c in causes])
agg_causes = (
    agg_causes
    .withColumn("total_cause_minutes", expr(total_expr))
)

for c in causes:
    agg_causes = agg_causes.withColumn(f"{c}_pct", expr(f"CASE WHEN total_cause_minutes>0 THEN round(100.0*sum_{c}/total_cause_minutes,2) ELSE null END"))



In [0]:
# === 6) Persist gold tables as Delta (partition for performance) ===
# monthly: partition by year/month
# (agg_monthly
#  .write
#  .format("delta")
#  .mode("overwrite")   # use append for incremental jobs; overwrite for first-run dev
#  .option("overwriteSchema", "true")
#  .partitionBy("year","month")
#  .save(gold_monthly_path)
# )

# # carrier-level: partition by carrier/year/month
# (agg_carrier
#  .write
#  .format("delta")
#  .mode("overwrite")
#  .option("overwriteSchema", "true")
#  .partitionBy("carrier","year","month")
#  .save(gold_carrier_path)
# )

# # delay causes kpi

# ( agg_causes
#     .write
#     .format("delta")
#     .mode("overwrite")
#     .option("overwriteSchema","true")
#     .partitionBy("year", "month")
#     .save(gold_causes_path)
# )




In [0]:
# register in the Hive metastore / Databricks catalog for SQL access
spark.sql(f"CREATE TABLE IF NOT EXISTS gold_monthly USING DELTA LOCATION '{gold_monthly_path}'")
spark.sql(f"CREATE TABLE IF NOT EXISTS gold_carrier USING DELTA LOCATION '{gold_carrier_path}'")
spark.sql(f"CREATE TABLE IF NOT EXISTS gold_causes USING DELTA LOCATION '{gold_causes_path}'")

print("Gold tables written and registered.")


Gold tables written and registered.


In [0]:
#  Variables: set your target parquet paths (adjust to your storage mount / abfss / wasbs path) ---


compression_codec = "snappy"   # fast + splittable -> good for parquet
target_repartition_files = 8   # tune for your cluster / file size needs (8 is an example)

def write_parquet(df, path, partition_by=None, mode="overwrite", repart_files=None, compression="snappy"):
    """
    df: Spark DataFrame
    path: destination path
    partition_by: list of partition column names (or None)
    mode: 'overwrite' for first-run dev; use 'append' for incremental jobs
    repart_files: None or int - if set, will call df.repartition(repart_files, *partition_by) when partition_by provided
    compression: parquet compression codec
    """
    writer = df
    # If repartition requested and partition columns exist, repartition by partition columns + target number
    if repart_files:
        if partition_by:
            writer = df.repartition(repart_files, *[col for col in partition_by])
        else:
            writer = df.repartition(repart_files)

    w = writer.write
    w = w.format("parquet").mode(mode).option("compression", compression)
    if partition_by:
        w = w.partitionBy(*partition_by)
    # For first-run / dev you may want to overwrite; for production incremental use append
    w.save(path)
    print(f"Wrote dataframe -> {path}  (mode={mode}, partition_by={partition_by}, files={repart_files}, compression={compression})")


# 1) monthly: partition by year/month

write_parquet(
    df = agg_monthly,
    path = gold_monthly_path,
    mode = "overwrite",             # change to "append" for incremental
    repart_files = target_repartition_files,
    compression = compression_codec
)


# 2) carrier-level: 
write_parquet(
    df = agg_carrier,
    path = gold_carrier_path,
    mode = "overwrite",
    repart_files = target_repartition_files,
    compression = compression_codec
)



# 3) delay causes KPI 

write_parquet(
    df = agg_causes,
    path = gold_causes_path,
    mode = "overwrite",
    repart_files = target_repartition_files,
    compression = compression_codec
)

write_parquet(
    df = df_k,
    path = gold_master_path,
    mode = "overwrite",
    repart_files = target_repartition_files,
    compression = compression_codec
)


# 4) Quick verification (Databricks helpers)

try:
    display(dbutils.fs.ls(gold_monthly_path))
    display(dbutils.fs.ls(gold_carrier_path))
    display(dbutils.fs.ls(gold_causes_path))
    display(dbutils.fs.ls(gold_master_path))
except Exception as e:
    print("dbutils not available; falling back to spark read-sample")
    # quick read sample
    print("Monthly sample:")
    spark.read.parquet(gold_monthly_path).limit(5).display()
    print("Carrier sample:")
    spark.read.parquet(gold_carrier_path).limit(5).display()
    print("Causes sample:")
    spark.read.parquet(gold_causes_path).limit(5).display()
    print("Causes sample:")
    spark.read.parquet(gold_master_path).limit(5).display()

Wrote dataframe -> /mnt/gold-parquet/airline_delays_gold/monthly  (mode=overwrite, partition_by=None, files=8, compression=snappy)
Wrote dataframe -> /mnt/gold-parquet/airline_delays_gold/carrier  (mode=overwrite, partition_by=None, files=8, compression=snappy)
Wrote dataframe -> /mnt/gold-parquet/airline_delays_gold/causes  (mode=overwrite, partition_by=None, files=8, compression=snappy)
Wrote dataframe -> /mnt/gold-parquet/airline_delays_gold/master  (mode=overwrite, partition_by=None, files=8, compression=snappy)


path name size modificationTime dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/_SUCCESS _SUCCESS 0 1762640803000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/_committed_2108347030398625207 _committed_2108347030398625207 816 1762640366000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/_committed_5258064619359259591 _committed_5258064619359259591 1626 1762640802000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/_started_2108347030398625207 _started_2108347030398625207 0 1762640365000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/_started_5258064619359259591 _started_5258064619359259591 0 1762640801000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00000-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-123-1.c000.snappy.parquet part-00000-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-123-1.c000.snappy.parquet 5677 1762640801000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00001-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-124-1.c000.snappy.parquet part-00001-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-124-1.c000.snappy.parquet 5674 1762640801000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00002-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-125-1.c000.snappy.parquet part-00002-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-125-1.c000.snappy.parquet 5831 1762640801000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00003-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-126-1.c000.snappy.parquet part-00003-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-126-1.c000.snappy.parquet 5673 1762640801000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00004-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-127-1.c000.snappy.parquet part-00004-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-127-1.c000.snappy.parquet 5683 1762640802000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00005-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-128-1.c000.snappy.parquet part-00005-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-128-1.c000.snappy.parquet 5657 1762640802000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00006-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-129-1.c000.snappy.parquet part-00006-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-129-1.c000.snappy.parquet 5679 1762640802000 dbfs:/mnt/gold-parquet/airline_delays_gold/monthly/part-00007-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-130-1.c000.snappy.parquet part-00007-tid-5258064619359259591-2d6c21ef-f1d9-4470-9a48-7b41a5ada167-130-1.c000.snappy.parquet 5677 1762640802000

path name size modificationTime dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/_SUCCESS _SUCCESS 0 1762640806000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/_committed_5481466059340698406 _committed_5481466059340698406 1626 1762640806000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/_committed_5847147899503606816 _committed_5847147899503606816 816 1762640369000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/_started_5481466059340698406 _started_5481466059340698406 0 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/_started_5847147899503606816 _started_5847147899503606816 0 1762640368000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00000-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-136-1.c000.snappy.parquet part-00000-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-136-1.c000.snappy.parquet 14920 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00001-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-137-1.c000.snappy.parquet part-00001-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-137-1.c000.snappy.parquet 15055 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00002-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-138-1.c000.snappy.parquet part-00002-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-138-1.c000.snappy.parquet 15136 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00003-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-139-1.c000.snappy.parquet part-00003-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-139-1.c000.snappy.parquet 15114 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00004-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-140-1.c000.snappy.parquet part-00004-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-140-1.c000.snappy.parquet 15012 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00005-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-141-1.c000.snappy.parquet part-00005-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-141-1.c000.snappy.parquet 14979 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00006-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-142-1.c000.snappy.parquet part-00006-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-142-1.c000.snappy.parquet 14978 1762640805000 dbfs:/mnt/gold-parquet/airline_delays_gold/carrier/part-00007-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-143-1.c000.snappy.parquet part-00007-tid-5481466059340698406-a254b36e-6ba1-4f03-9665-bca3ee0b6ad1-143-1.c000.snappy.parquet 14914 1762640805000

path name size modificationTime dbfs:/mnt/gold-parquet/airline_delays_gold/causes/_SUCCESS _SUCCESS 0 1762640809000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/_committed_4452467296939432791 _committed_4452467296939432791 1632 1762640809000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/_committed_5367492173537244362 _committed_5367492173537244362 822 1762640372000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/_started_4452467296939432791 _started_4452467296939432791 0 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/_started_5367492173537244362 _started_5367492173537244362 0 1762640371000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00000-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-149-1.c000.snappy.parquet part-00000-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-149-1.c000.snappy.parquet 9044 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00001-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-150-1.c000.snappy.parquet part-00001-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-150-1.c000.snappy.parquet 9032 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00002-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-151-1.c000.snappy.parquet part-00002-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-151-1.c000.snappy.parquet 9081 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00003-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-152-1.c000.snappy.parquet part-00003-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-152-1.c000.snappy.parquet 9079 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00004-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-153-1.c000.snappy.parquet part-00004-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-153-1.c000.snappy.parquet 9028 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00005-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-154-1.c000.snappy.parquet part-00005-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-154-1.c000.snappy.parquet 9036 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00006-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-155-1.c000.snappy.parquet part-00006-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-155-1.c000.snappy.parquet 9158 1762640808000 dbfs:/mnt/gold-parquet/airline_delays_gold/causes/part-00007-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-156-1.c000.snappy.parquet part-00007-tid-4452467296939432791-f4f48876-44fc-4f67-8c7e-b75012c14363-156-1.c000.snappy.parquet 9093 1762640808000

path name size modificationTime dbfs:/mnt/gold-parquet/airline_delays_gold/master/_SUCCESS _SUCCESS 0 1762640813000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/_committed_7318516604140017921 _committed_7318516604140017921 824 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/_started_7318516604140017921 _started_7318516604140017921 0 1762640811000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00000-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-161-1.c000.snappy.parquet part-00000-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-161-1.c000.snappy.parquet 470677 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00001-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-162-1.c000.snappy.parquet part-00001-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-162-1.c000.snappy.parquet 469383 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00002-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-163-1.c000.snappy.parquet part-00002-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-163-1.c000.snappy.parquet 470854 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00003-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-164-1.c000.snappy.parquet part-00003-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-164-1.c000.snappy.parquet 471004 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00004-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-165-1.c000.snappy.parquet part-00004-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-165-1.c000.snappy.parquet 476317 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00005-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-166-1.c000.snappy.parquet part-00005-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-166-1.c000.snappy.parquet 475071 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00006-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-167-1.c000.snappy.parquet part-00006-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-167-1.c000.snappy.parquet 477059 1762640812000 dbfs:/mnt/gold-parquet/airline_delays_gold/master/part-00007-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-168-1.c000.snappy.parquet part-00007-tid-7318516604140017921-10e68129-c4ca-43db-add3-a2625b59b589-168-1.c000.snappy.parquet 477249 1762640812000

In [0]:
from pyspark.sql import DataFrame

def inspect_dataframe(df: DataFrame, name: str, sample_rows: int = 5):
    print(f"\n {name} SCHEMA ")
    df.printSchema()

    print(f"\n  {name} COLUMN TYPES ")
    for field in df.schema.fields:
        print(f"{field.name:30}  →  {field.dataType}")

    print(f"\n  {name} SAMPLE DATA (first {sample_rows} rows) ")
    display(df.limit(sample_rows))

# Inspect all your key DataFrames
inspect_dataframe(agg_carrier, "agg_carrier")
inspect_dataframe(agg_monthly, "agg_monthly")
inspect_dataframe(agg_causes, "agg_causes")


===== 🔎 agg_carrier SCHEMA =====
root
 |-- carrier: string (nullable = true)
 |-- carrier_name: string (nullable = true)
 |-- year: integer (nullable = true)
 |-- month: integer (nullable = true)
 |-- total_arr_flights: double (nullable = true)
 |-- total_arr_del15: double (nullable = true)
 |-- total_arr_delay_minutes: double (nullable = true)
 |-- total_arr_cancelled: double (nullable = true)
 |-- total_arr_diverted: double (nullable = true)
 |-- sum_carrier_ct: double (nullable = true)
 |-- sum_weather_ct: double (nullable = true)
 |-- sum_nas_ct: double (nullable = true)
 |-- sum_security_ct: double (nullable = true)
 |-- sum_late_aircraft_ct: double (nullable = true)
 |-- delay_rate: double (nullable = true)
 |-- avg_delay_per_flight: double (nullable = true)
 |-- cancel_rate: double (nullable = true)
 |-- divert_rate: double (nullable = true)
 |-- carrier_ct_pct: double (nullable = true)
 |-- weather_ct_pct: double (nullable = true)
 |-- nas_ct_pct: double (nullable = true)
 |--

carrier carrier_name year month total_arr_flights total_arr_del15 total_arr_delay_minutes total_arr_cancelled total_arr_diverted sum_carrier_ct sum_weather_ct sum_nas_ct sum_security_ct sum_late_aircraft_ct delay_rate avg_delay_per_flight cancel_rate divert_rate carrier_ct_pct weather_ct_pct nas_ct_pct security_ct_pct late_aircraft_ct_pct 9E Endeavor Air Inc. 2025 2 16896.0 3312.0 243201.0 339.0 41.0 681.68 121.50000000000001 1241.4599999999996 1.44 1265.9599999999998 0.19602272727272727 14.393998579545455 0.020063920454545456 0.0024266098484848485 0.20581877030470652 0.03668433956111643 0.37483242956002943 4.347773577613798E-4 0.38222968321638634 OH PSA Airlines Inc. 2024 5 18829.0 5329.0 429500.0 178.0 64.0 1206.2900000000002 333.8700000000002 1532.06 17.5 2239.230000000001 0.28302087205905785 22.810558181528492 0.009453502575813904 0.0033990121620903926 0.2263654190788054 0.06265211720883103 0.28749753703825326 0.0032839489955807425 0.42020097767852965 G7 GoJet Airlines LLC d/b/a United Express 2025 2 5220.0 1394.0 140921.0 150.0 6.0 289.44 25.21 461.64999999999986 0.0 617.72 0.2670498084291188 26.996360153256706 0.028735632183908046 0.0011494252873563218 0.207629732715456 0.01808438903315591 0.3311645457023571 0.0 0.4431213325490309 G7 GoJet Airlines LLC d/b/a United Express 2024 11 5558.0 1435.0 137827.0 40.0 14.0 303.82 8.28 503.42 0.16 619.2900000000001 0.25818639798488663 24.797948902482908 0.007196833393306945 0.0025188916876574307 0.21172568067625105 0.005770155473633595 0.350822665282201 1.1150058886248492E-4 0.4315699979790519 QX Horizon Air 2025 1 7754.0 1285.0 66695.0 143.0 32.0 324.39000000000004 59.44 372.63 2.64 525.95 0.1657209182357493 8.601367036368327 0.018442094402888833 0.0041269022440030955 0.2524337574413447 0.046255009532703 0.28997315279561103 0.002054394770631493 0.4092836854597097


===== 🔎 agg_monthly SCHEMA =====
root
 |-- year: integer (nullable = true)
 |-- month: integer (nullable = true)
 |-- year_month: string (nullable = false)
 |-- total_arr_flights: double (nullable = true)
 |-- total_arr_del15: double (nullable = true)
 |-- total_arr_delay_minutes: double (nullable = true)
 |-- total_arr_cancelled: double (nullable = true)
 |-- total_arr_diverted: double (nullable = true)
 |-- sum_carrier_ct: double (nullable = true)
 |-- sum_weather_ct: double (nullable = true)
 |-- sum_nas_ct: double (nullable = true)
 |-- sum_security_ct: double (nullable = true)
 |-- sum_late_aircraft_ct: double (nullable = true)
 |-- delay_rate: double (nullable = true)
 |-- avg_delay_per_flight: double (nullable = true)
 |-- cancel_rate: double (nullable = true)
 |-- divert_rate: double (nullable = true)
 |-- carrier_ct_pct: double (nullable = true)
 |-- weather_ct_pct: double (nullable = true)
 |-- nas_ct_pct: double (nullable = true)
 |-- security_ct_pct: double (nullable = tru

year month year_month total_arr_flights total_arr_del15 total_arr_delay_minutes total_arr_cancelled total_arr_diverted sum_carrier_ct sum_weather_ct sum_nas_ct sum_security_ct sum_late_aircraft_ct delay_rate avg_delay_per_flight cancel_rate divert_rate carrier_ct_pct weather_ct_pct nas_ct_pct security_ct_pct late_aircraft_ct_pct 2024 12 2024-12 631944.0 132515.0 9585044.0 4579.0 1752.0 43489.29000000008 5391.969999999997 34704.26999999997 308.71999999999974 48620.75999999997 0.20969421341131492 15.16755282113605 0.007245895205904321 0.0027723975542136643 0.3281838789432237 0.040689503777722964 0.2618893512516051 0.0023296983488889276 0.36690756767855937 2024 8 2024-08 660639.0 150010.0 1.129244E7 13434.0 2174.0 46480.130000000005 6147.579999999993 41086.280000000086 331.8900000000001 55964.15999999992 0.22706803564427774 17.093208242322962 0.020334857615127173 0.0032907533463813064 0.30984679425457123 0.040981123663456076 0.273890200949217 0.002212451913218609 0.37306942921953706 2025 5 2025-05 667586.0 155262.0 1.1438449E7 7549.0 1898.0 43212.07000000002 7216.090000000004 49775.120000000024 203.42 54855.019999999975 0.23257228282198847 17.134045651047206 0.011307906397078429 0.002843079393516341 0.27831760462269783 0.04647694228815707 0.32058848761948544 0.0013101748454158561 0.3533067906242438 2025 4 2025-04 644084.0 124749.0 8747498.0 5291.0 1443.0 37564.129999999925 4662.500000000001 36994.31999999997 231.10999999999993 45297.05999999998 0.19368436415125978 13.5812999546643 0.0082147670179666 0.002240391004899982 0.3011173946557696 0.03737501314638537 0.2965497472046296 0.0018525982387691405 0.3631052467544463 2024 6 2024-06 651799.0 157404.0 1.1642182E7 8315.0 2105.0 50697.429999999935 6373.670000000002 38325.49000000005 435.89000000000016 61571.86999999999 0.2414916254857709 17.86161377970816 0.012757000240871803 0.0032295232119104204 0.3220840465971871 0.040492337092335774 0.24348431285412414 0.002769237317774256 0.39117006613857874


===== 🔎 agg_causes SCHEMA =====
root
 |-- carrier: string (nullable = true)
 |-- carrier_name: string (nullable = true)
 |-- year: integer (nullable = true)
 |-- month: integer (nullable = true)
 |-- sum_carrier_ct: double (nullable = true)
 |-- sum_weather_ct: double (nullable = true)
 |-- sum_nas_ct: double (nullable = true)
 |-- sum_security_ct: double (nullable = true)
 |-- sum_late_aircraft_ct: double (nullable = true)
 |-- total_cause_minutes: double (nullable = true)
 |-- carrier_ct_pct: double (nullable = true)
 |-- weather_ct_pct: double (nullable = true)
 |-- nas_ct_pct: double (nullable = true)
 |-- security_ct_pct: double (nullable = true)
 |-- late_aircraft_ct_pct: double (nullable = true)


===== 🧩 agg_causes COLUMN TYPES =====
carrier                         →  StringType()
carrier_name                    →  StringType()
year                            →  IntegerType()
month                           →  IntegerType()
sum_carrier_ct                  →  DoubleType()
sum_w

carrier carrier_name year month sum_carrier_ct sum_weather_ct sum_nas_ct sum_security_ct sum_late_aircraft_ct total_cause_minutes carrier_ct_pct weather_ct_pct nas_ct_pct security_ct_pct late_aircraft_ct_pct 9E Endeavor Air Inc. 2025 2 681.68 121.50000000000001 1241.4599999999996 1.44 1265.9599999999998 3312.039999999999 20.58 3.67 37.48 0.04 38.22 OH PSA Airlines Inc. 2024 5 1206.2900000000002 333.8700000000002 1532.06 17.5 2239.230000000001 5328.950000000001 22.64 6.27 28.75 0.33 42.02 G7 GoJet Airlines LLC d/b/a United Express 2025 2 289.44 25.21 461.64999999999986 0.0 617.72 1394.02 20.76 1.81 33.12 0.0 44.31 G7 GoJet Airlines LLC d/b/a United Express 2024 11 303.82 8.28 503.42 0.16 619.2900000000001 1434.97 21.17 0.58 35.08 0.01 43.16 QX Horizon Air 2025 1 324.39000000000004 59.44 372.63 2.64 525.95 1285.0500000000002 25.24 4.63 29.0 0.21 40.93